In [1]:
import os
import time
os.environ["CUDA_LAUNCH_BLOCKING"] = "1"
from os import listdir
import pandas as pd
import numpy as np
import glob
import cv2
import json
from os.path import expanduser
import splitfolders
import shutil
from define_path import Def_Path

from tqdm import tqdm

import torch 
import torchvision
from torchvision import models
from torchvision.models.detection.rpn import AnchorGenerator
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import torch.nn as nn 
import torchvision.transforms as T
from torchvision.transforms import functional as F
from torchsummary import summary

from sklearn.model_selection import train_test_split

import albumentations as A # Library for augmentations

import matplotlib.pyplot as plt 
from PIL import Image

import transforms, utils, engine, train
from utils import collate_fn
from engine import train_one_epoch, evaluate

t = torch.cuda.get_device_properties(0).total_memory
print(t)
torch.cuda.empty_cache()

r = torch.cuda.memory_reserved(0)
print(r)
a = torch.cuda.memory_allocated(0)
print(a)
# f = r-a  # free inside reserved

weights_path = '/home/jc-merlab/Pictures/Data/trained_models/keypointsrcnn_weights_sim_b1_e25_v0.pth'

16908615680
0
0


In [2]:
# to generalize home directory. User can change their parent path without entering their home directory
path = Def_Path()

parent_path =  path.home + "/Pictures/" + "Data/"

root_dir = parent_path + path.year + "-" + path.month + "-" + path.day + "/"

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
# torch.cuda.set_per_process_memory_fraction(0.9, 0)
print(device)

cuda


In [4]:
def train_transform():
    return A.Compose([
        A.Sequential([
            A.RandomRotate90(p=1), # Random rotation of an image by 90 degrees zero or more times
            A.RandomBrightnessContrast(brightness_limit=0.2, contrast_limit=0.3, brightness_by_max=True, always_apply=False, p=1), # Random change of brightness & contrast
        ], p=1)
#         A.Resize(640, 480)  # Resize all images to be 640x480
    ],
    keypoint_params=A.KeypointParams(format='xy'), # More about keypoint formats used in albumentations library read at https://albumentations.ai/docs/getting_started/keypoints_augmentation/
    bbox_params=A.BboxParams(format='pascal_voc', label_fields=['bboxes_labels']) # Bboxes should have labels, read more at https://albumentations.ai/docs/getting_started/bounding_boxes_augmentation/
    )

In [5]:
def train_test_split(src_dir):
    dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_img) and os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_img)
        os.mkdir(dst_dir_anno)
        
    for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
        shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = parent_path + "split_folder_output" + "-" + path.year + "-" + path.month + "-" + path.day 
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(.7, .2, .1), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
    shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  

In [6]:
class KPDataset(Dataset):
    def __init__(self, root, transform=None, demo=False):                
        self.root = root
        self.transform = transform
        self.demo = demo # Use demo=True if you need transformed and original images (for example, for visualization purposes)
        self.imgs_files = sorted(os.listdir(os.path.join(root, "images")))
        self.annotations_files = sorted(os.listdir(os.path.join(root, "annotations")))
    
    def __getitem__(self, idx):
        img_file = self.imgs_files[idx]
        img_path = os.path.join(self.root, "images", self.imgs_files[idx])
        annotations_path = os.path.join(self.root, "annotations", self.annotations_files[idx])

        img_original = cv2.imread(img_path)
        img_original = cv2.cvtColor(img_original, cv2.COLOR_BGR2RGB)
        
        with open(annotations_path) as f:
            data = json.load(f)
            bboxes_original = data['bboxes']
            keypoints_original = data['keypoints']
            
            # All objects are keypoints on the robot
            bboxes_labels_original = [] 
            bboxes_labels_original.append('base_joint')
            bboxes_labels_original.append('joint2')
            bboxes_labels_original.append('joint3')
            bboxes_labels_original.append('joint4')
            bboxes_labels_original.append('joint5')
            bboxes_labels_original.append('joint6')  

        if self.transform:   
            # Converting keypoints from [x,y,visibility]-format to [x, y]-format + Flattening nested list of keypoints            
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]], where each keypoint is in [x, y]-format            
            # Then we need to convert it to the following list:
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2]
            keypoints_original_flattened = [el[0:2] for kp in keypoints_original for el in kp]
            
            # Apply augmentations
            transformed = self.transform(image=img_original, bboxes=bboxes_original, bboxes_labels=bboxes_labels_original, keypoints=keypoints_original_flattened)
            img = transformed['image']
            bboxes = transformed['bboxes']
            # Unflattening list transformed['keypoints']
            # For example, if we have the following list of keypoints for three objects (each object has two keypoints):
            # [obj1_kp1, obj1_kp2, obj2_kp1, obj2_kp2, obj3_kp1, obj3_kp2], where each keypoint is in [x, y]-format
            # Then we need to convert it to the following list:
            # [[obj1_kp1, obj1_kp2], [obj2_kp1, obj2_kp2], [obj3_kp1, obj3_kp2]]
            keypoints_transformed_unflattened = np.reshape(np.array(transformed['keypoints']), (-1,1,2)).tolist()

            # Converting transformed keypoints from [x, y]-format to [x,y,visibility]-format by appending original visibilities to transformed coordinates of keypoints
            keypoints = []
            for o_idx, obj in enumerate(keypoints_transformed_unflattened):
#                 print("object", obj)
#                 print(" obj index", o_idx)# Iterating over objects
                obj_keypoints = []
                for k_idx, kp in enumerate(obj): # Iterating over keypoints in each object
                    obj_keypoints.append(kp + [keypoints_original[o_idx][k_idx][2]])
                keypoints.append(obj_keypoints)
        
        else:
            img, bboxes, keypoints = img_original, bboxes_original, keypoints_original        
        
        # Convert everything into a torch tensor        
        bboxes = torch.as_tensor(bboxes, dtype=torch.float32)       
        target = {}
        labels = [1, 2, 3, 4, 5, 6]            
        target["boxes"] = bboxes
        target["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are joint positions
        target["image_id"] = torch.tensor([idx])
        target["area"] = (bboxes[:, 3] - bboxes[:, 1]) * (bboxes[:, 2] - bboxes[:, 0])
        target["iscrowd"] = torch.zeros(len(bboxes), dtype=torch.int64)
        target["keypoints"] = torch.as_tensor(keypoints, dtype=torch.float32)
        img = F.to_tensor(img)        
        bboxes_original = torch.as_tensor(bboxes_original, dtype=torch.float32)
        target_original = {}
        target_original["boxes"] = bboxes_original
        target_original["labels"] = torch.as_tensor(labels, dtype=torch.int64) # all objects are glue tubes
        target_original["image_id"] = torch.tensor([idx])
        target_original["area"] = (bboxes_original[:, 3] - bboxes_original[:, 1]) * (bboxes_original[:, 2] - bboxes_original[:, 0])
        target_original["iscrowd"] = torch.zeros(len(bboxes_original), dtype=torch.int64)
        target_original["keypoints"] = torch.as_tensor(keypoints_original, dtype=torch.float32)        
        img_original = F.to_tensor(img_original)

        if self.demo:
            return img, target, img_original, target_original, img_file
        else:
            return img, target, img_file
    
    def __len__(self):
        return len(self.imgs_files)

In [7]:
# import torch
# import torch.nn.functional as functional
# from torch.nn import Sequential as Seq, Linear, ReLU
# from torch_geometric.nn import GATConv
# from torch_geometric.data import Data

# class GAT(torch.nn.Module):
#     def __init__(self):
#         super(GAT, self).__init__()
#         self.conv1 = GATConv(5, 16, heads=4, dropout=0.4)
#         self.conv2 = GATConv(64, 16, heads=4, dropout=0.4)
#         self.conv3 = GATConv(64, 16, heads=4, dropout=0.4)  # New layer
#         self.conv4 = GATConv(64, 32, heads=4, dropout=0.4)  # New layer

#     def forward(self, x, edge_index):
#         x = functional.elu(self.conv1(x, edge_index))
#         x = functional.elu(self.conv2(x, edge_index))
#         x = functional.elu(self.conv3(x, edge_index))  # Use the new layer
#         x = self.conv4(x, edge_index)  # Use the new layer
#         return x  # This is the predicted keypoints. Shape should be [num_nodes, num_node_features]

In [8]:
import torch
import torch.nn.functional as func
from torch_geometric.nn import GCNConv
from torch_geometric.data import Data

class KeyPointGNN(torch.nn.Module):
    def __init__(self):
        super(KeyPointGNN, self).__init__()
        # Define graph convolution layers
        self.conv1 = GCNConv(5, 256) # 5 features for each keypoint
        self.conv2 = GCNConv(256, 128)
        self.conv3 = GCNConv(128,64)
        self.fc = torch.nn.Linear(64, 5) # Output 5 values (x, y, c, v, label) for each keypoint
        
        # Linear layers for edge feature prediction
        self.edge_fc1 = torch.nn.Linear(2, 128) # Assuming edge_features has 2 elements
        self.edge_fc2 = torch.nn.Linear(128, 2) # Output size depends on your edge features

    def forward(self, data):
        x, edge_index, edge_features = data.x, data.edge_index, data.edge_attr
        # Graph convolution layers
        x = func.relu(self.conv1(x, edge_index))
        x = func.relu(self.conv2(x, edge_index))
        x = func.relu(self.conv3(x, edge_index))
        # Fully connected layer to output keypoint locations
        x = self.fc(x)
        
        # Linear layers for edge feature prediction
        edge_features = func.relu(self.edge_fc1(edge_features))
        predicted_edge_features = self.edge_fc2(edge_features)
        
        return x, predicted_edge_features

In [9]:
class KeypointPipeline(nn.Module):
    def __init__(self, weights_path, num_vertices, delta=1.0):
        super().__init__()

        self.keypoint_model = torch.load(weights_path).to(device)
        self.num_vertices = num_vertices
        self.delta = delta

        # Integrate the GAT model
        self.gcn = KeyPointGNN().to(device)

    def get_node_features(self, keypoints):
        node_features = []
        for keypoint in keypoints:
            x, y, confidence, visibility, label = keypoint
            node_features.append([x, y, confidence, visibility, label])
        return torch.tensor(node_features, dtype=torch.float).to(device)

    def get_edge_features(self, keypoints):
        edges = [(0,1), (1, 2), (2, 3), (3, 4), (4, 5), (5, 0)]
        edge_features = []
        for edge in edges:
            k1, k2 = keypoints[edge[0]][:2], keypoints[edge[1]][:2]
            distance = torch.norm(k1 - k2)
            angle = torch.atan2(k2[1] - k1[1], k2[0] - k1[0])
            edge_features.append([distance.item(), angle.item()])
        return torch.tensor(edges, dtype=torch.long).t().contiguous().to(device), \
               torch.tensor(edge_features, dtype=torch.float).to(device)

    def process_model_output(self, output):
        scores = output[0]['scores'].detach().cpu().numpy()
        high_scores_idxs = np.where(scores > 0.7)[0].tolist()

        post_nms_idxs = torchvision.ops.nms(output[0]['boxes'][high_scores_idxs], 
                                            output[0]['scores'][high_scores_idxs], 0.3).cpu().numpy()

        confidence = output[0]['scores'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()
        labels = output[0]['labels'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()
        keypoints = []
        for idx, kps in enumerate(output[0]['keypoints'][high_scores_idxs][post_nms_idxs].detach().cpu().numpy()):
            # Setting t_i = 1 because label is found
            keypoints.append(list(map(int, kps[0,0:2])) + [confidence[idx]] + [1] + [labels[idx]])

        # Create a dictionary where the key is the label and the value is the keypoint
        label_to_keypoint = {}
        for keypoint in keypoints:
            label = keypoint[-1]
            if label not in label_to_keypoint or label_to_keypoint[label][-2] < keypoint[-2]:
                label_to_keypoint[label] = keypoint

        # Use a dictionary to keep track of all possible keypoints and their locations.
        # Initialize with placeholders for missing keypoints.
        all_keypoints = {i: [-1, -1, 0, 0, i] for i in range(1, self.num_vertices+1)}  # added another 0 for t_i

        for label, keypoint in label_to_keypoint.items():
            all_keypoints[label] = keypoint

        keypoints = list(all_keypoints.values())
        keypoints = torch.stack([torch.tensor(kp) for kp in keypoints]).float().to(device)
#         print("processed keypoints", keypoints)

        # Now process these keypoints with GAT
        node_features = self.get_node_features(keypoints)
        edges, edge_features = self.get_edge_features(node_features)      
                
        data = Data(x=node_features, edge_index=edges, edge_attr=edge_features)
        print("graph data", data)
        
        print("node feature", data.x)
        print("edges", data.edge_index)
        print("edge feature", data.edge_attr)
        
        vertices_pred, edge_pred = self.gcn(data)
        return vertices_pred, edge_pred, edge_features 
    
    def process_image(self, img):
        img = img.unsqueeze(0).to(device)
        # Temporarily set the keypoint model to evaluation mode
        keypoint_model_training = self.keypoint_model.training  # Save the current mode
        self.keypoint_model.eval()
        with torch.no_grad():
            output = self.keypoint_model(img)
        # Set the keypoint model back to its previous mode
        self.keypoint_model.train(keypoint_model_training)
        img = (img[0].permute(1,2,0).detach().cpu().numpy() * 255).astype(np.uint8)
        labeled_keypoints = self.process_model_output(output)
        
        return labeled_keypoints        

    def forward(self, imgs):
        outputs = []

        for i in range(imgs.shape[0]):
            pred_keypoints = self.process_image(imgs[i])
            outputs.append((pred_keypoints))  # Each output now contains both predicted and original keypoints

        return outputs

    def loss_function(self, vertices_pred, vertices_orig, pred_edge_features, orig_edge_features):
        # Assume both tensors are of the shape [num_nodes, num_node_features] and the first two features are x and y.
#         pos_loss = functional.mse_loss(pred[:, :3], orig[:, :3])  # Loss based on position of keypoints
        # Compute differences
        diff = (vertices_pred[:, :3] - vertices_orig[:, :3]).abs()

        # Compute Huber loss
        huber_loss = torch.where(diff < self.delta, 0.5 * diff**2, self.delta * (diff - 0.5 * self.delta))
        pos_loss = huber_loss.mean()
        # Compute loss for edge features
        edge_loss = func.mse_loss(pred_edge_features, orig_edge_features)

        vis_loss = func.cross_entropy(vertices_pred[:, 3], vertices_orig[:, 3])  # Loss based on visibility of keypoints

        return pos_loss + vis_loss
#         return pos_loss

In [ ]:
import torch.optim as optim

num_epochs = 25  # Define your number of epochs
batch_size = 8

KEYPOINTS_FOLDER_TRAIN = train_test_split(root_dir) +"/train" #train_test_split(root_dir) +"/train"
KEYPOINTS_FOLDER_VAL = train_test_split(root_dir) +"/val"
KEYPOINTS_FOLDER_TEST = train_test_split(root_dir) +"/test"

dataset_train = KPDataset(KEYPOINTS_FOLDER_TRAIN, transform=None, demo=False)
dataset_val = KPDataset(KEYPOINTS_FOLDER_VAL, transform=None, demo=False)
dataset_test = KPDataset(KEYPOINTS_FOLDER_TEST, transform=None, demo=False)

data_loader_train = DataLoader(dataset_train, batch_size=batch_size, shuffle=True, collate_fn=collate_fn)
data_loader_val = DataLoader(dataset_val, batch_size=1, shuffle=False, collate_fn=collate_fn)
data_loader_test = DataLoader(dataset_test, batch_size=1, shuffle=False, collate_fn=collate_fn)


model = KeypointPipeline(weights_path, num_vertices=6)  # Initialize the model with the provided weights and vertices
model = model.to(device)  # Ensure the model is on the right device

optimizer = optim.Adam(model.parameters(), lr=0.005)  # Define the optimizer

v=2

for epoch in range(num_epochs):
    start_time = time.time()
    model.train()  # Ensure the model is in training mode    

    # Training loop
    for i, batch in enumerate(data_loader_train):
        img_tuple, target_dict_tuple, img_files = batch
        
        imgs = [img.to(device) for img in img_tuple]  # Create list of images
        
        # Process each image individually
        total_train_loss = 0
        for i in range(len(imgs)):
            img = imgs[i].unsqueeze(0)  # Unsqueeze to add batch dimension
            
            # Prepare ground truth vertices for the image
            keypoints = target_dict_tuple[i]['keypoints'].to(device)
            visibility = torch.ones((keypoints.shape[0], keypoints.shape[1], 1)).to(device)
            vertices_gt = torch.cat((keypoints, visibility), dim=2).unsqueeze(0)  # Unsqueeze to add batch dimension
            
            vertices_gt = vertices_gt.squeeze()
            
            print("ground truth keypoints", vertices_gt.shape)
                        
            optimizer.zero_grad()  # Clear the gradients

            outputs = model(img)  # Forward pass
            
            vertices_pred, edge_pred, edge_features = outputs[0]

            loss = model.loss_function(vertices_pred, vertices_gt, edge_pred, edge_features)  # Compute the loss
            loss.backward()  # Backpropagate the loss

            optimizer.step()  # Update the model parameters

            total_train_loss += loss.item()

    end_time = time.time()
    epoch_time = end_time - start_time
    eta = epoch_time * (num_epochs - epoch - 1)
    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {loss.item()}, ETA: {eta} seconds')
    

    model.eval()  # Ensure the model is in evaluation mode
    

    # Validation loop
    with torch.no_grad():  # No need to track gradients in validation
        for i, batch in enumerate(data_loader_val):
            img_tuple, target_dict_tuple, img_files = batch
            imgs = [img.to(device) for img in img_tuple]  # Create list of images          

            
            total_val_loss = 0
            for i in range(len(imgs)):
                img = imgs[i].unsqueeze(0)  # Unsqueeze to add batch dimension
                # Prepare ground truth vertices for the image
                keypoints = target_dict_tuple[i]['keypoints'].to(device)
                visibility = torch.ones((keypoints.shape[0], keypoints.shape[1], 1)).to(device)
                vertices_gt = torch.cat((keypoints, visibility), dim=2).unsqueeze(0)  # Unsqueeze to add batch dimension

                vertices_gt = vertices_gt.squeeze()
                
                outputs = model(img)  # Forward pass
            
                vertices_pred, edge_pred, edge_features = outputs[0]

                loss = model.loss_function(vertices_pred, vertices_gt, edge_pred, edge_features)  # Compute the loss

                total_val_loss += loss.item()

        print(f'Validation Loss after epoch {epoch + 1}: {total_val_loss/len(data_loader_val)}')
    
model_save_path = f"/home/jc-merlab/Pictures/Data/trained_models/keypointsrcnn_weights_gcn_b{batch_size}_e{num_epochs}_v{v}.pth"
torch.save(model, model_save_path)

Copying files: 2662 files [00:00, 18580.05 files/s]
Copying files: 2662 files [00:00, 18734.06 files/s]
Copying files: 2662 files [00:00, 18690.69 files/s]


ground truth keypoints torch.Size([6, 4])
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [256.0000, 203.0000,   0.9997,   1.0000,   3.0000],
        [278.0000, 203.0000,   0.9998,   1.0000,   4.0000],
        [363.0000, 253.0000,   0.9993,   1.0000,   5.0000],
        [369.0000, 274.0000,   0.9795,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.0250,  -1.5958],
        [ 22.0000,   0.0000],
        [ 98.6154,   0.5317],
        [ 21.8403,   1.2925],
        [144.8102,   2.4442]], device='cuda:0')
ground truth keypoints torch.Size([6, 4])
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.99

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [178.0000, 276.0000,   0.9998,   1.0000,   3.0000],
        [180.0000, 256.0000,   0.9996,   1.0000,   4.0000],
        [209.0000, 161.0000,   0.9993,   1.0000,   5.0000],
        [225.0000, 146.0000,   0.9970,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.3057,  -3.0543],
        [ 20.0998,  -1.4711],
        [ 99.3277,  -1.2745],
        [ 21.9317,  -0.7532],
        [223.4502,   1.4226]], device='cuda:0')
ground truth keypoints torch.Size([6, 4])
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [282.0000

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [257.0000, 203.0000,   0.9997,   1.0000,   3.0000],
        [278.0000, 203.0000,   0.9999,   1.0000,   4.0000],
        [374.0000, 179.0000,   0.9994,   1.0000,   5.0000],
        [394.0000, 186.0000,   0.9977,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.0062,  -1.5833],
        [ 21.0000,   0.0000],
        [ 98.9545,  -0.2450],
        [ 21.1896,   0.3367],
        [226.4001,   2.2152]], device='cuda:0')
ground truth keypoints torch.Size([6, 4])
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [257.0000

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [194.0000, 235.0000,   0.9998,   1.0000,   3.0000],
        [206.0000, 218.0000,   0.9998,   1.0000,   4.0000],
        [297.0000, 177.0000,   0.9988,   1.0000,   5.0000],
        [319.0000, 174.0000,   0.9980,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 8.4000e+01, -1.5708e+00],
        [ 8.0000e+01, -2.4981e+00],
        [ 2.0809e+01, -9.5613e-01],
        [ 9.9810e+01, -4.2331e-01],
        [ 2.2204e+01, -1.3553e-01],
        [ 2.0241e+02,  1.8769e+00]], device='cuda:0')
ground truth keypoints torch.Size([6, 4])
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [257.0000, 283.0000,   0.9999,   

...

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   1.0000,   1.0000,   2.0000],
        [282.0000, 206.0000,   0.9996,   1.0000,   3.0000],
        [301.0000, 213.0000,   0.9999,   1.0000,   4.0000],
        [332.0000, 119.0000,   0.9991,   1.0000,   5.0000],
        [326.0000,  97.0000,   0.9981,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.6536,  -1.2687],
        [ 20.2485,   0.3530],
        [ 98.9798,  -1.2522],
        [ 22.8035,  -1.8370],
        [278.4313,   1.8175]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   1.0000,   1.0000,   2.0000],
        [282.0000, 207.0000,   0.9997,   1.0000,   3.0000],

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [283.0000, 207.0000,   0.9998,   1.0000,   3.0000],
        [302.0000, 214.0000,   0.9999,   1.0000,   4.0000],
        [402.0000, 223.0000,   0.9995,   1.0000,   5.0000],
        [419.0000, 236.0000,   0.9975,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 8.4000e+01, -1.5708e+00],
        [ 8.0006e+01, -1.2530e+00],
        [ 2.0248e+01,  3.5299e-01],
        [ 1.0040e+02,  8.9758e-02],
        [ 2.1401e+01,  6.5285e-01],
        [ 2.0756e+02,  2.4586e+00]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [283.0000, 207.

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [284.0000, 207.0000,   0.9997,   1.0000,   3.0000],
        [303.0000, 214.0000,   0.9999,   1.0000,   4.0000],
        [363.0000, 293.0000,   0.9988,   1.0000,   5.0000],
        [382.0000, 305.0000,   0.9961,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.3243,  -1.2412],
        [ 20.2485,   0.3530],
        [ 99.2018,   0.9212],
        [ 22.4722,   0.5633],
        [138.6362,   2.6779]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [284.0000, 207.0000,   0.9998,   1.0000,   3.0000],

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [281.0000, 206.0000,   0.9998,   1.0000,   3.0000],
        [301.0000, 213.0000,   0.9999,   1.0000,   4.0000],
        [368.0000, 285.0000,   0.9990,   1.0000,   5.0000],
        [387.0000, 276.0000,   0.9982,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.3617,  -1.2805],
        [ 21.1896,   0.3367],
        [ 98.3514,   0.8214],
        [ 21.0238,  -0.4424],
        [157.8670,   2.5272]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [281.0000, 207.0000,   0.9999,   1.0000,   3.0000],

graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [283.0000, 207.0000,   0.9998,   1.0000,   3.0000],
        [302.0000, 214.0000,   0.9999,   1.0000,   4.0000],
        [390.0000, 167.0000,   0.9982,   1.0000,   5.0000],
        [397.0000, 146.0000,   0.9986,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
edge feature tensor([[ 84.0000,  -1.5708],
        [ 80.0062,  -1.2530],
        [ 20.2485,   0.3530],
        [ 99.7647,  -0.4905],
        [ 22.1359,  -1.2490],
        [261.0785,   2.1322]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6], edge_attr=[6, 2])
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [282.0000, 207.0000,   0.9998,   1.0000,   3.0000],

In [ ]:
def visualize_and_save(img, vertices, filename):
    print("type of image befor conversion",type(img))    
    print("type of vertices before conversion", type(vertices))
    print(img.shape)
    img = (img.permute(1,2,0).cpu().numpy() * 255).astype(np.uint8)
#     img = (img * 255).astype(np.uint8)  # Convert back from [0, 1] range to [0, 255]
    img = cv2.cvtColor(img, cv2.COLOR_RGB2BGR)
    vertices = vertices.cpu().numpy()

    print(f"Image shape before saving: {img.shape}")  # print the image shape
    print("type of vertices", type(vertices))
#     print("entered vertices", vertices)
#     print("entered image", img)

    # Convert grayscale to BGR if necessary
    if len(img.shape) == 2:
        img = cv2.cvtColor(img, cv2.COLOR_GRAY2BGR)
        
    for i in range(vertices.shape[0]):
        img = cv2.circle(img, (int(vertices[i, 0]), int(vertices[i, 1])), radius=2, color=(0, 0, 255), thickness=-1)
        
    result = cv2.imwrite(filename, img)
    print(f"Image saved at {filename}: {result}")  # print if save was successful

In [12]:
# Test loop
model.eval()  # Ensure the model is in evaluation mode

predicted_keypoints = []  # List to store predicted keypoints

with torch.no_grad():  # No need to track gradients in testing
    for idx, batch in enumerate(data_loader_test):
        img_tuple, target_dict_tuple, img_files = batch
        imgs = [img.to(device) for img in img_tuple]  # Create list of images
        total_test_loss = 0
        for i in range(len(imgs)):
            img = imgs[i].unsqueeze(0)  # Unsqueeze to add batch dimension
            # Prepare ground truth vertices for the image
            keypoints = target_dict_tuple[i]['keypoints'].to(device)
            visibility = torch.ones((keypoints.shape[0], keypoints.shape[1], 1)).to(device)
            vertices_gt = torch.cat((keypoints, visibility), dim=2).unsqueeze(0)  # Unsqueeze to add batch dimension
            vertices_gt = vertices_gt.squeeze()
            outputs = model(img)  # Forward pass
            
            vertices_pred, edge_pred, edge_features = outputs[0]

            loss = model.loss_function(vertices_pred, vertices_gt, edge_pred, edge_features)  # Compute the loss
            
            # Visualize and save the prediction
            filename = f'/home/jc-merlab/Pictures/Data/occ_vis_data/image_{idx}_{i}.jpg'
            visualize_and_save(img.squeeze(), outputs[0], filename)
            print(f"Image saved at {filename}")  # Print statement to confirm image save

            total_test_loss += loss.item()
            predicted_keypoints.extend(outputs)

print(f'Test Loss: {total_test_loss/len(data_loader_test)}')

# Print predicted keypoints
for i, keypoints in enumerate(predicted_keypoints):
    print(f'Predicted keypoints for test image {i+1}:')
    print(keypoints)

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [179.0000, 298.0000,   0.9992,   1.0000,   3.0000],
        [176.0000, 278.0000,   0.9997,   1.0000,   4.0000],
        [230.0000, 195.0000,   0.9985,   1.0000,   5.0000],
        [249.0000, 203.0000,   0.9990,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[2.2546e+02, 2.9266e+02, 1.2432e+00, 1.5663e+01, 5.3155e-01],
        [2.3406e+02, 2.5065e+02, 1.3871e+00, 2.3402e+01, 1.7239e+00],
        [1.9220e+02, 2.9283e+02, 1.2403e+00, 2.2330e+01, 3.0466e+00],
        [1.7609e+02, 2.8986e+02, 1.2269e+00, 1.9566e+01, 9.9270e-01],
        [1.5578e+02, 2.2135e+02, 1.1688e+00, 1.7402e+01, 1.8980e+00],
        [2.0704e+02, 2.0629e+02, 1.3256e+00, 1.8514e+01, 8.9773e-02]],
       device='cuda:0')
tensor([[2.2546e+02, 2.9266e+02, 1.2432

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9998,   1.0000,   2.0000],
        [180.0000, 298.0000,   0.9993,   1.0000,   3.0000],
        [176.0000, 277.0000,   0.9998,   1.0000,   4.0000],
        [ 82.0000, 247.0000,   0.9682,   1.0000,   5.0000],
        [ 91.0000, 229.0000,   0.9950,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[204.8647, 286.6986,   1.4274,  21.1123,  -8.2913],
        [182.3133, 296.9978,   1.2701,  20.8366,  -0.9822],
        [181.6741, 301.9070,   1.2424,  20.2023,   0.8210],
        [176.1339, 289.6951,   1.2267,  19.5743,   1.0141],
        [137.8368, 235.7143,   1.1483,  15.3547,  -0.4136],
        [150.4346, 238.2005,   1.2340,  16.5267,  -4.3341]], device='cuda:0')
tensor([[204.8647, 286.6986,   1.4274,  21.1123,  -8.2913],
        [182.3133, 296.9978,   1.2701,  20.836

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [178.0000, 275.0000,   0.9995,   1.0000,   3.0000],
        [180.0000, 254.0000,   0.9997,   1.0000,   4.0000],
        [ 84.0000, 227.0000,   0.9992,   1.0000,   5.0000],
        [ 63.0000, 221.0000,   0.9925,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[257.5299, 320.2375,   1.5712,  28.9470,  -8.6776],
        [206.9497, 317.7556,   1.3451,  23.7866,  -1.5951],
        [177.1309, 293.7907,   1.2314,  19.7521,   0.7888],
        [171.5409, 275.9766,   1.2103,  19.1673,   1.4599],
        [132.8994, 213.9893,   1.1238,  14.8053,   0.7259],
        [172.8432, 234.8968,   1.2820,  20.8308,  -3.2593]], device='cuda:0')
tensor([[257.5299, 320.2375,   1.5712,  28.9470,  -8.6776],
        [206.9497, 317.7556,   1.3451,  23.786

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [178.0000, 276.0000,   0.9999,   1.0000,   3.0000],
        [180.0000, 255.0000,   0.9998,   1.0000,   4.0000],
        [183.0000, 157.0000,   0.9972,   1.0000,   5.0000],
        [190.0000, 136.0000,   0.9982,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[250.8037, 316.0510,   1.2034,  26.5600,   6.4714],
        [252.9153, 277.5642,   1.3977,  27.4955,   4.6399],
        [186.2645, 278.1837,   1.2249,  21.7054,   3.1853],
        [171.7407, 276.5783,   1.2110,  19.1785,   1.4422],
        [158.0558, 194.5357,   1.1946,  16.6807,   0.4902],
        [196.5480, 162.9188,   1.2115,  25.3903,   8.1573]], device='cuda:0')
tensor([[250.8037, 316.0510,   1.2034,  26.5600,   6.4714],
        [252.9153, 277.5642,   1.3977,  27.495

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [178.0000, 277.0000,   0.9998,   1.0000,   3.0000],
        [179.0000, 256.0000,   0.9998,   1.0000,   4.0000],
        [252.0000, 189.0000,   0.9983,   1.0000,   5.0000],
        [273.0000, 181.0000,   0.9957,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[ 2.4886e+02,  3.3280e+02,  1.1935e+00,  1.3794e+01,  4.6906e+00],
        [ 2.4811e+02,  2.6895e+02,  1.3866e+00,  2.2521e+01,  1.8742e+00],
        [ 1.9345e+02,  2.7460e+02,  1.2441e+00,  2.2539e+01,  3.3886e+00],
        [ 1.7184e+02,  2.7707e+02,  1.2115e+00,  1.9175e+01,  1.4196e+00],
        [ 1.6877e+02,  1.9586e+02,  1.2295e+00,  1.7511e+01, -1.3949e-01],
        [ 2.6281e+02,  1.8411e+02,  1.4407e+00,  1.7773e+01,  1.5997e+00]],
       device='cuda:0')
tensor([[

...

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [257.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [311.0000, 224.0000,   0.9995,   1.0000,   3.0000],
        [326.0000, 238.0000,   0.9998,   1.0000,   4.0000],
        [347.0000, 332.0000,   0.9979,   1.0000,   5.0000],
        [332.0000, 334.0000,   0.9822,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[ 3.3341e+02,  2.4195e+02,  1.6758e+00,  2.6023e+01, -2.8669e+00],
        [ 2.4511e+02,  2.7642e+02,  1.4206e+00,  2.5992e+01, -2.0454e-01],
        [ 2.2079e+02,  2.6652e+02,  1.3442e+00,  2.4103e+01,  9.4942e-01],
        [ 3.1514e+02,  2.2138e+02,  1.6065e+00,  2.1895e+01, -2.5786e+00],
        [ 3.3371e+02,  3.4886e+02,  1.4022e+00,  1.1848e+01, -2.1024e+00],
        [ 3.1677e+02,  3.5150e+02,  1.4062e+00,  1.6481e+01, -1.6532e+00]],
       device='cuda:0')
tensor([[

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [311.0000, 223.0000,   0.9996,   1.0000,   3.0000],
        [326.0000, 237.0000,   0.9999,   1.0000,   4.0000],
        [424.0000, 238.0000,   0.9989,   1.0000,   5.0000],
        [438.0000, 251.0000,   0.9971,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[275.6816, 367.5541,   1.7032,  12.9022,  28.8751],
        [254.8914, 318.3418,   1.6031,  22.2096,  11.8986],
        [295.7380, 207.7221,   1.5814,  22.0566,  -4.8026],
        [317.1696, 221.8307,   1.6087,  21.6697,  -2.6077],
        [377.4172, 226.0740,   1.5522,   3.6347,  11.1665],
        [407.6966, 214.2728,   1.6342,  -1.7782,  12.8635]], device='cuda:0')
tensor([[275.6816, 367.5541,   1.7032,  12.9022,  28.8751],
        [254.8914, 318.3418,   1.6031,  22.209

node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 283.0000,   0.9999,   1.0000,   2.0000],
        [311.0000, 224.0000,   0.9991,   1.0000,   3.0000],
        [327.0000, 238.0000,   0.9999,   1.0000,   4.0000],
        [413.0000, 190.0000,   0.9952,   1.0000,   5.0000],
        [432.0000, 193.0000,   0.9956,   1.0000,   6.0000]], device='cuda:0')
edges tensor([[0, 1, 2, 3, 4, 5],
        [1, 2, 3, 4, 5, 0]], device='cuda:0')
graph data Data(x=[6, 5], edge_index=[2, 6])
tensor([[269.5481, 350.4940,   1.6192,  24.7302,  34.0898],
        [256.5885, 305.6808,   1.5426,  24.1580,  21.3563],
        [287.0021, 210.2461,   1.5624,  22.3875,  -4.3336],
        [316.3336, 221.6105,   1.6083,  21.8102,  -2.5937],
        [383.7020, 157.2187,   1.6558,  10.0143,  14.0176],
        [400.1443, 163.6794,   1.6003,  10.0055,  22.4134]], device='cuda:0')
tensor([[269.5481, 350.4940,   1.6192,  24.7302,  34.0898],
        [256.5885, 305.6808,   1.5426,  24.158

tensor([[273.1716, 364.9753,   1.6257,  25.3249,  35.8625],
        [257.7780, 304.6498,   1.5340,  24.6807,  23.8340],
        [284.6958, 209.8241,   1.5569,  22.3564,  -4.2329],
        [316.2456, 221.2605,   1.6086,  21.8251,  -2.5938],
        [372.4141, 150.4080,   1.6254,  11.6827,  14.0862],
        [387.3554, 171.3087,   1.5760,  13.8498,  24.7852]], device='cuda:0')
type of image befor conversion <class 'torch.Tensor'>
type of vertices before conversion <class 'torch.Tensor'>
torch.Size([3, 480, 640])
Image shape before saving: (480, 640, 3)
type of vertices <class 'numpy.ndarray'>
Image saved at /home/jc-merlab/Pictures/Data/occ_vis_data/image_131_0.jpg: True
Image saved at /home/jc-merlab/Pictures/Data/occ_vis_data/image_131_0.jpg
node feature tensor([[258.0000, 367.0000,   1.0000,   1.0000,   1.0000],
        [258.0000, 282.0000,   0.9999,   1.0000,   2.0000],
        [311.0000, 224.0000,   0.9995,   1.0000,   3.0000],
        [327.0000, 238.0000,   0.9999,   1.0000,   4.00

tensor([[250.8037, 316.0510,   1.2034,  26.5600,   6.4714],
        [252.9153, 277.5642,   1.3977,  27.4955,   4.6399],
        [186.2645, 278.1837,   1.2249,  21.7054,   3.1853],
        [171.7407, 276.5783,   1.2110,  19.1785,   1.4422],
        [158.0558, 194.5357,   1.1946,  16.6807,   0.4902],
        [196.5480, 162.9188,   1.2115,  25.3903,   8.1573]], device='cuda:0')
Predicted keypoints for test image 20:
tensor([[249.5020, 322.7293,   1.1975,  24.8396,   6.7265],
        [256.2923, 280.9303,   1.4129,  26.5505,   3.7791],
        [186.7922, 278.3188,   1.2261,  21.7719,   3.2053],
        [171.6437, 276.4691,   1.2108,  19.1636,   1.4374],
        [157.5196, 194.3782,   1.1930,  16.6285,   0.5076],
        [197.2839, 165.4866,   1.2193,  24.7359,   7.9859]], device='cuda:0')
Predicted keypoints for test image 21:
tensor([[ 2.4351e+02,  3.1187e+02,  1.1911e+00,  1.6979e+01,  6.7269e+00],
        [ 2.4734e+02,  2.6796e+02,  1.4000e+00,  2.3679e+01,  2.4507e+00],
        [ 1.8906